In [1]:
import import_ipynb #Allows you to import ipynb files
from queue import PriorityQueue
from dataclasses import dataclass
import time
import matplotlib.pyplot as plt
from matplotlib import colors

from reedsshepp import *
from vehicle import *
from Grid import Grid
from utils import *

from IPython.core.display import HTML
display(HTML("<style>pre { white-space: pre !important; }</style>"))
np.set_printoptions(threshold=np.inf)

importing Jupyter notebook from reedsshepp.ipynb
importing Jupyter notebook from vehicle.ipynb
importing Jupyter notebook from utils.ipynb
importing Jupyter notebook from Grid.ipynb
importing Jupyter notebook from GVD.ipynb


In [2]:
@dataclass
class Cell:
    """The cell is the discretized position that the vehicleState falls into"""
    col: int = -1
    row: int = -1
    ori: float = 0.0
    rev: float = 0.0
    def reset(self):
        self.col = -1
        self.row = -1
        self.ori = 0
        self.rev = 0
    def __eq__(self, other):
        return self.col == other.col and self.row == other.row and self.ori == other.ori

In [3]:
#Node class that the A* will be referencing to check and compare costs
class HybridAStarNode:
    
    def __init__(self, parent=None, cell:Cell=None, vehicleState:VehicleState=None, rsAction:ReedsSheppAction=None):
        self.cell = cell
        self.vehicleState = vehicleState #Even though cell and vehicle state store the same thing, cell is discrete and vehiclestate is nondiscrete
        self.reedsSheppAction = rsAction
        self.parent = parent
        self.g = 0 #distance to start node
        self.h = 0 #distance to goal node
        
        self.rsindex = -1
    def FCost(self):
        return self.g + self.h
    
    def __eq__(self, other):
        return self.cell == other.cell
    
    def __lt__(self, other):
        return self.FCost() < other.FCost()
    
    def __gt__(self, other):
        return self.FCost() > other.FCost()
    def __repr__(self):
        return 'Point(x=%s, y=%s, ori=%s, rev=%s)' % (self.cell.col, self.cell.row, np.rad2deg(self.cell.ori), self.cell.rev)

In [4]:
#This will implement the basic A* Algorithm
class HybridAStar:
    #class variables
    def __init__(self, grid:Grid, vehicle:Vehicle, debug:bool=False):
        self._grid = grid
        self._vehicle = vehicle
        self.currentCostMap = [[float('inf') for i in range(self._grid.width)] for j in range(self._grid.height)]
        self._debug = debug
        self.rs = ReedsShepp(self._vehicle)
        
    def ReedsSheppPath(self, current:VehicleState, goal:VehicleState):
        x,y = current.position
        ori = current.orientation
        x1,y1 = goal.position
        ori1 = goal.orientation
        return self.rs.run_optimalpath(start=(x,y,ori), end=(x1,y1,ori1))

    #Generates the Path
    def GeneratePath(self, current):
        path = []
        states = []
        while current is not None:
            path.append((current.cell.row, current.cell.col))
            states.append(current.vehicleState)
            current = current.parent
        return path[::-1], states[::-1]
    
    #Calculates distance heuristic
    def CalculateDistance(self, current, destination):
        return np.sqrt(((current.vehicleState.position[0] - destination.vehicleState.position[0]) ** 2 + (current.vehicleState.position[1] - destination.vehicleState.position[1]) ** 2))
    
    #gets all neighbors at current node
    def GetNextNodes(self, current_state:VehicleState, gear, end:VehicleState):
        nodes = []
        positions = []
        for steer in self._vehicle.steers:
            newVehicleState, length = self._vehicle.getNextState(current_state, steer, gear, 1)
            #self._grid.IsSafe(newVehicleState, 1.5)
            positions.append((newVehicleState.position, newVehicleState.orientation))
            if(IsPointInGrid(newVehicleState.position, (self._grid.width, self._grid.height))):
                nodes.append(HybridAStarNode(None, None, newVehicleState, ReedsSheppAction(steer, gear, length)))
        #check reeds shepp path
        #add to child if its cheap af
        rspath = self.ReedsSheppPath(current_state, end)
        statePath = self.rs.discretizePath(current_state, rspath, 1, 1)
        
        if(self._debug):
            print(positions)
        return nodes
    
    def statetoCell(self, state:VehicleState):
        x = int(np.floor(state.position[0]))
        y = int(np.floor(state.position[1]))
        theta = mod2Pi(state.orientation)
        rev = 1 if state.gear==Gear.Backward else 0
        return Cell(row=x, col=y, ori=theta, rev=rev)
    
    def run(self, start:VehicleState, end:VehicleState):
        start_node = HybridAStarNode(None, self.statetoCell(start), start, ReedsSheppAction(Steer.Straight, Gear.Forward, 0))
        end_node = HybridAStarNode(None, self.statetoCell(end), end)
        
        open_list = PriorityQueue()
        closed_list = []
        open_list.put(start_node)
        voro = self._grid.returnVoroDistanceMap()
        
        while open_list.qsize():
            current_node = open_list.get()
            closed_list.append(current_node)
            if(current_node == end_node):
                return self.GeneratePath(current_node)
            if(self._debug):
                print("Current Position: " + str(current_node.vehicleState.position))
                print("End Position: " + str(end_node.vehicleState.position))
                print("Current Cell: " + str((current_node.cell.row, current_node.cell.col)))
                print("End Cell: " + str((end_node.cell.row, end_node.cell.col)))
                print("Current Angle: " + str((current_node.cell.ori)))
                print("End Angle: " + str((end_node.cell.ori)))
                print()

            for gear in self._vehicle.gears:
                nextNodes = self.GetNextNodes(current_node.vehicleState, gear, end)
                for nextNode in nextNodes:
                    nextNode.g = current_node.g + 1 #path cost
                    nextNode.h = self.CalculateDistance(nextNode, end_node) #hueristic
                    nextNode.parent = current_node
                    nextNode.cell = self.statetoCell(nextNode.vehicleState)
                    
                    if(nextNode.FCost() < self.currentCostMap[nextNode.cell.col][nextNode.cell.row]):
                        if(nextNode in open_list.queue): continue
                        self.currentCostMap[nextNode.cell.col][nextNode.cell.row] = nextNode.FCost()
                        open_list.put(nextNode)
                        
            if(self._debug):
                print()
                for i,row in enumerate(hastar.currentCostMap):
                    printer = []
                    for q,cost in enumerate(row):
                        if((i,q) == (current_node.cell.col, current_node.cell.row)):
                            printer.append("XXXX")
                        elif(cost != float('inf')):
                            printer.append("{:.2f}".format(cost))
                        elif((i,q) == (end_node.cell.col, end_node.cell.row)):
                            printer.append("YYYY")
                        else:
                            printer.append("     ")
                    print(printer)




In [5]:
v = Vehicle((1,1))
rows, cols = 31, 31
g = Grid(rows, cols)
obstacle_list = [(0,0), (30,30), (15,15), (0,30), (30,0), (15,0), (0,15), (30,15), (15,30)]
[g.AddObstacle(obs) for obs in obstacle_list]
obs_X = [cell[0] for cell in g.obstacleCells]
obs_Y = [cell[1] for cell in g.obstacleCells]

In [11]:
start = VehicleState((29,24),np.deg2rad(180))
end = VehicleState((6,6),np.deg2rad(0))
path = []
hastar = HybridAStar(g, v, True)
path, states = hastar.run(start,end)

path_X = [cell[0] for cell in path] 
path_Y = [cell[1] for cell in path]

state_X = [state.position[0] for state in states] 
state_Y = [state.position[1] for state in states]
state_O = [state.orientation for state in states]

Current Position: (29, 24)
End Position: (6, 6)
Current Cell: (29, 24)
End Cell: (6, 6)
Current Angle: -3.141592653589793
End Angle: 0.0

[((28.0, 24.0), 3.141592653589793), ((28.158529015192105, 23.54030230586814), 4.141592653589793), ((28.158529015192105, 24.45969769413186), 2.141592653589793)]
[((30.0, 24.0), 3.141592653589793), ((29.841470984807895, 23.54030230586814), 2.141592653589793), ((29.841470984807895, 24.45969769413186), 4.141592653589793)]

['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ',

['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '29.91', '29.66', '29.43', '31.15', '31.00']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     

['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '30.05', '29.79', '29.54', '29.32', '29.26', '30.60', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '30.17', '29.91', '29.66', '29.43', '31.15', '31.00']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     

[((17.647325203932425, 17.798005492521423), 3.141592653589793), ((17.80585421912453, 17.33830779838956), 4.141592653589793), ((17.80585421912453, 18.257703186653284), 2.141592653589793)]
[((19.647325203932425, 17.798005492521423), 3.141592653589793), ((19.48879618874032, 17.33830779838956), 2.141592653589793), ((19.48879618874032, 18.257703186653284), 4.141592653589793)]

['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '

[((21.569400800476597, 19.177098574917007), 2.141592653589793), ((21.096924936626245, 19.06212041730962), 1.1415926535897931), ((21.870569479416353, 19.55887186559304), 3.141592653589793)]

['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ']
['     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     ', '     

...

['42.82', '41.14', '39.54', '38.04', '36.68', '35.48', '34.46', '33.62', '32.94', '32.41', '31.99', '31.66', '31.39', '31.17', '30.99', '30.95', '30.97', '31.38', '31.43', '31.30', '31.25', '32.21', '32.87', '33.28', '33.39', '34.23', '35.13', '36.09', '37.69', '39.62', '41.64']
['41.23', '39.66', '38.18', '36.82', '35.60', '34.52', '33.59', '32.81', '32.16', '31.63', '31.20', '30.84', '30.55', '30.30', '30.24', '30.55', '30.53', '30.93', '30.89', '30.92', '31.09', '31.60', '32.72', '32.68', '32.77', '33.58', '34.47', '35.30', '36.21', '38.12', '40.04']
['42.15', '40.61', '39.15', '37.79', '36.55', '35.44', '34.46', '33.62', '32.90', '32.29', '31.77', '31.34', '30.98', '30.68', '30.41', '30.19', '30.14', '30.11', '30.44', '30.45', '30.98', '30.94', '30.89', '32.11', '32.63', '32.58', '33.38', '34.66', '37.34', '38.17', '     ']
['43.11', '41.57', '40.11', '38.74', '37.47', '36.31', '35.28', '34.36', '33.56', '32.87', '32.28', '31.77', '31.34', '30.97', '30.65', '30.38', '30.14', '30.08

['     ', '     ', '     ', '     ', '     ', '     ', '50.02', '50.46', '49.39', '48.36', '47.37', '46.89', '45.98', '45.12', '44.72', '43.94', '43.68', '42.97', '42.30', '42.79', '42.36', '41.53', '40.95', '40.87', '40.34', '39.84', '39.85', '40.20', '39.78', '40.51', '41.13']
Current Position: (6.145343354632489, 27.331870350476212)
End Position: (6, 6)
Current Cell: (6, 27)
End Cell: (6, 6)
Current Angle: -0.14159265358979312
End Angle: 0.0

[((7.135335851232934, 27.190750342416344), 6.141592653589793), ((7.043265858000285, 27.668219226213047), 7.141592653589793), ((6.913520773398304, 26.758024690422907), 5.141592653589793)]
[((5.155350858032044, 27.47299035853608), 6.141592653589793), ((5.377165935866675, 27.905716010529517), 5.141592653589793), ((5.247420851264693, 26.995521474739377), 7.141592653589793)]

['48.35', '46.64', '45.05', '43.58', '42.16', '41.06', '40.07', '40.69', '40.84', '40.51', '40.15', '39.86', '39.79', '39.18', '39.09', '39.05', '39.53', '40.47', '41.31', '42.

[((4.159300742966874, 29.472352357329427), 6.141592653589793), ((4.381115820801504, 29.905078009322864), 5.141592653589793), ((4.251370736199523, 28.994883473532724), 7.141592653589793)]

['48.35', '46.64', '45.05', '43.58', '42.16', '41.06', '40.07', '40.69', '40.84', '40.51', '40.15', '39.86', '39.79', '39.18', '39.09', '39.05', '39.53', '40.47', '41.31', '42.33', '42.00', '42.54', '43.03', '44.00', '44.69', '45.90', '46.81', '49.70', '51.67', '50.85', '52.26']
['46.68', '44.89', '43.23', '41.69', '40.21', '40.59', '39.01', '38.34', '39.36', '38.52', '38.24', '38.03', '37.87', '37.75', '38.19', '38.61', '38.19', '39.15', '39.80', '41.03', '41.66', '41.34', '41.83', '42.80', '43.72', '44.72', '45.64', '49.04', '48.78', '49.73', '51.16']
['45.53', '43.20', '41.45', '39.83', '38.33', '38.27', '37.06', '36.74', '36.22', '37.59', '37.36', '37.19', '37.06', '36.97', '36.89', '37.05', '37.01', '37.89', '38.92', '39.80', '40.71', '40.53', '40.68', '41.65', '42.40', '43.57', '44.33', '45.27',

[((3.1693082463664286, 29.613472365389296), 6.141592653589793), ((3.077238253133779, 30.090941249185995), 7.141592653589793), ((2.947493168531798, 29.180746713395862), 5.141592653589793)]
[((1.189323253165538, 29.895712381509032), 6.141592653589793), ((1.411138331000169, 30.328438033502465), 5.141592653589793), ((1.2813932463981879, 29.418243497712332), 7.141592653589793)]

['48.35', '46.64', '45.05', '43.58', '42.16', '41.06', '40.07', '40.69', '40.84', '40.51', '40.15', '39.86', '39.79', '39.18', '39.09', '39.05', '39.53', '40.47', '41.31', '42.33', '42.00', '42.54', '43.03', '44.00', '44.69', '45.90', '46.81', '49.70', '51.67', '50.85', '52.26']
['46.68', '44.89', '43.23', '41.69', '40.21', '40.59', '39.01', '38.34', '39.36', '38.52', '38.24', '38.03', '37.87', '37.75', '38.19', '38.61', '38.19', '39.15', '39.80', '41.03', '41.66', '41.34', '41.83', '42.80', '43.72', '44.72', '45.64', '49.04', '48.78', '49.73', '51.16']
['45.53', '43.20', '41.45', '39.83', '38.33', '38.27', '37.06',

TypeError: cannot unpack non-iterable NoneType object

In [ ]:
#PRINTER
#colormap
cmap = colors.ListedColormap(['white', 'black'])
bounds = [0,.5,1]
norm = colors.BoundaryNorm(bounds, cmap.N)

fig, ax = plt.subplots()
#x.imshow(data,extent=[0, rows, 0, cols], cmap=cmap, norm=norm)
ax.plot(start.position[0], start.position[1], marker='.', color='green', linestyle='none', MarkerSize=40)
x, y, a, b = start.position[0], start.position[1], 1, np.rad2deg(start.orientation)
x1, y1 = rpoint(x,y,a,b)
plt.arrow(x, y, (x1-x)/2, (y1-y)/2, head_width = .4, width = .1,color='green')
ax.plot(end.position[0], end.position[1], marker='.', color='red', linestyle='none', MarkerSize=40)
x, y, a, b = end.position[0], end.position[1], 1, np.rad2deg(end.orientation)
x1, y1 = rpoint(x,y,a,b)
plt.arrow(x, y, (x1-x)/2, (y1-y)/2, head_width = .4, width = .1,color='red')

ax.plot(path_X, path_Y, marker='.', color='blue', MarkerSize=10)
ax.plot(state_X, state_Y, marker='*', color='purple', MarkerSize=10)
#draw gridlines
ax.grid(which='major', axis='both', linestyle='-', color='k', linewidth=1)
ax.set_xticks(np.arange(0, rows, 1));
ax.set_yticks(np.arange(0, cols, 1));
for index in range(len(state_O)):
    x, y, a, b = state_X[index], state_Y[index], 1, np.rad2deg(state_O[index])
    x1, y1 = rpoint(x,y,a,b)
    plt.arrow(x, y, (x1-x)/2, (y1-y)/2, head_width = .4, width = .1,)
    
plt.rcParams['figure.figsize'] = [18, 18]
plt.show()

In [1]:
# import matplotlib.pyplot as plt
# from matplotlib import colors


In [ ]:
# start = VehicleState((38, 40),np.deg2rad(120))
# end = VehicleState((5, 9),np.deg2rad(300))
# v = Vehicle((1,1))
# rs = ReedsShepp(v)
# startTuple = (start.position[0], start.position[1], np.rad2deg(start.orientation))
# endTuple = (end.position[0], end.position[1], np.rad2deg(end.orientation))
# rspath = rs.run_optimalpath(startTuple, endTuple)
# statePath = rs.discretizePath(start, rspath, 1, 1)
# state_X = [state.position[0] for state in statePath] 
# state_Y = [state.position[1] for state in statePath]
# state_O = [state.orientation for state in statePath]